# Traffic flows on a map

Exploratory maps taking a look at whether we can merge PeMS data with SHN postmile segments.

Notes:
* maps look like certain highways are missing - some interstates, as well as state routes (boulevards)....is this expected? some stations are missing, maybe 200ish out of 4,000 as we merge things together. do more work to look at which freeways are present in original PeMS.
* some districts don't have detectors? there are some districts with very few detectors, but 2-3 districts have no detectors...expected?

In [1]:
import geopandas as gpd
import pandas as pd

from utils import PROCESSED_GCS
from shared_utils.shared_data import GCS_FILE_PATH as SHARED_GCS

from stations_with_shn_postmiles import postmiles_to_pems_format

In [2]:
postmile_segments = gpd.read_parquet(
    f"{SHARED_GCS}state_highway_network_postmile_segments.parquet",
).pipe(postmiles_to_pems_format)

metric = "flow"
df = pd.read_parquet(
    f"{PROCESSED_GCS}station_daytype_hour_{metric}.parquet"
)

In [3]:
merge_cols = ["freeway_id", "freeway_direction", "abs_pm"]

station_postmiles_crosswalk = pd.read_parquet(
    f"{PROCESSED_GCS}stations_postmiles_crosswalk.parquet",
    columns = [
        "station_uuid", "routetype", 
        "city_id", "county_id", "district_id", 
        "station_type", "length", "physical_lanes"
    ] + merge_cols
)

In [4]:
df2 = df.groupby("station_uuid").agg({"tot_flow": "sum"}).reset_index()

In [5]:
gdf = pd.merge(
    postmile_segments,
    station_postmiles_crosswalk,
    on = merge_cols,
    how = "inner",
).merge(
    df2,
    on = "station_uuid",
    how = "inner"
)

In [6]:
gdf.shape

(4465, 15)

In [7]:
station_postmiles_crosswalk.shape

(4344, 11)

In [8]:
df2.shape

(4242, 2)

In [9]:
gdf.district_id.value_counts()

12    1096
8     1032
7      773
4      732
3      681
11     130
5       17
10       4
Name: district_id, dtype: int64

In [10]:
def make_map(gdf, district):
    return gdf[gdf.district_id==district].explore(
        "tot_flow", tiles="CartoDB Positron"
    )

In [11]:
make_map(gdf, 4)

In [12]:
make_map(gdf, 7)

In [13]:
make_map(gdf, 3)

In [14]:
make_map(gdf, 8)

In [15]:
make_map(gdf, 10)

In [16]:
make_map(gdf, 11)

In [17]:
make_map(gdf, 12)